In [1]:
from IPython.display import HTML

HTML('''<script>
  function code_toggle() {
    if (code_shown){
      $('div.input').hide('500');
      $('#toggleButton').val('Show Code')
    } else {
      $('div.input').show('500');
      $('#toggleButton').val('Hide Code')
    }
    code_shown = !code_shown
  }

  $( document ).ready(function(){
    code_shown=false;
    $('div.input').hide()
  });
</script>
<form action="javascript:code_toggle()"><input type="submit" id="toggleButton" value="Show Code"></form>''')

# Visualizing 3D Uncertainty of Forest Plots Measured with Error
David Diaz

# Motivation
The confident co-registration of remotely-sensed data and ground-based forest observations presents a distinct hurdle to fully leveraging the exceptionally high resolution of modern remote sensing technologies for precise predictive modeling of forest conditions across large landscapes where the remotely-sensed data have been collected. Misalignment between field-based plots and remotely-sensed data introduces error into predictive models trained to classify or quantify forest conditions. These imputation models are built to use remotely-sensed data using field plots as training examples, and applied to generate wall-to-wall forest inventory maps that “fill in the gaps” between forest plots on the ground using remotely-sensed data. Efforts to more precisely and accurately co-register field plots with remotely sensed data can thus help reduce the error introduced into this predictive modeling approach and increase the precision with which a predictive model may be able to distinguish varying forest conditions across the landscape.

# Objective
Using a probabilistic programming approach, I will incrementally build a data-generating, or *generative* model that will stochastically simulate the locations and shapes of trees on a forest inventory plot.This model will enable the incorporation of prior knowledge of common tree forms and expected levels of measurement error in field observations.

Each major step in composing the data generation model will be accompanied with an interactive visualization allowing the viewer to adjust the parameters of each stage in the model see how it affects a 3D representation of a tree or a forest inventory plot.

The main purpose of this visualization workflow is to confirm that the generative model behaves the way it is intended to. That is, whether the parameters being implemented have the desired effects on the 3D objects being modeled.

# Interacting with the vizualizations below
The graphics below were created with the plotly library, which provides python bindings to the plotly.js library which offers access to react.js and webgl. Each of the visualizations is interactive, but only some include widgets. All of the graphics can be zoomed and turned using your mouse. 

## Plot Layout for the Forest Inventory & Analysis (FIA) Program
<img src='./images/Measurements_Plot500.jpg' width='400' align='left'>

In [2]:
import numpy as np
import rasterio
from matplotlib import pyplot as plt
import ipywidgets as widgets
from ipywidgets import interact, Layout
import plotly.graph_objs as go
from plotly.offline import init_notebook_mode, iplot
init_notebook_mode(connected=True)

<img src='./images/nasa_terrain.jpg' width='400' align='right'>

# 0. Terrain where plot is installed


Using a lidar-derived bare-earth model, we will visualize a 3-D mesh or contour map of the terrain.

## Interactions
No widgets. The user can rotate and zoom a 3D model of the terrain.

In [3]:
src = rasterio.open('./data/lee_terrain_clipped.tif')
# bounding box of image
l,b,r,t = src.bounds
#resolution of image
res = src.res
terrain_x = np.arange(l,r, res[0])
terrain_y = np.arange(t,b, -res[0])
terrain_z = src.read(1)
z_aspect = (np.max(terrain_z) - np.min(terrain_z))/(r-l)

In [4]:
# create the trace in the figure for the terrain surface
terrain = go.Surface(x=terrain_x, y=terrain_y, z=terrain_z, hoverinfo='z',
                   contours={'x':{'highlight':False},'y':{'highlight':False}})

# we'll use this later in other graphs when we don't want the hoverinfo and interactivity
static_terrain = go.Surface(x=terrain_x, y=terrain_y, z=terrain_z, hoverinfo='none',
                   contours={'x':{'highlight':False},'y':{'highlight':False},'z':{'highlight':False}})

data = [terrain]
scene = {
    'xaxis': {'title':'Eastings', 'showgrid':False, 'showticklabels':False, 'zeroline':False, 'showspikes':False},
    'yaxis': {'title':'Northings', 'showgrid':False, 'showticklabels':False, 'zeroline':False, 'showspikes':False},
    'zaxis': {'title':'', 'showgrid':False, 'showticklabels':False, 'zeroline':False,  'showspikes':False},
    'camera':{'up':{'x':0, 'y':0, 'z':1},
              'center':{'x':0, 'y':0, 'z':0},
              'eye':{'x':0.2, 'y':-1.3, 'z':0.35}
             },
    'aspectmode':'manual',
    'aspectratio': {'x':1, 'y':1, 'z':z_aspect}
}

layout = go.Layout(
    title = '<b>Terrain Map</b> <br> (hover for elevation contour)',
    scene = scene,
    showlegend = False
)
fig = go.Figure(data=data, layout=layout)
iplot(fig)

# 1. Location of subplot 1 on the terrain
<img src='./images/step01.jpg' width='400' align='right'>
The center of FIA subplot 1 is calculated from GPS measurements in the field, projected to a UTM coordinate system with X,Y location calculated and assumed to include normally-distributed measurement error in both X and Y directions.

$ X_{plot}[1] \sim N(obs_x, \sigma_{GPS}) $

$ Y_{plot}[1] \sim N(obs_y, \sigma_{GPS}) $

## Interactions
The user can adjust the X or Y location of the subplot on the terrain.

In [5]:
def get_elev(x,y):
    '''gets the elevations from a raster at certain x,y coordinates'''
    if np.isscalar(x):
        row, col = src.index(x,y)
        elev = terrain_z[row,col]
    elif isinstance(x, np.ndarray):
        elev = []
        for coord in zip(x,y):
            row, col = src.index(*coord)
            elev.append(terrain_z[row,col]+2.0)
    return elev

def get_plot_boundary(x, y, radius, dynamic_elev=True):
    '''takes plot center and calculates points on circle'''
    theta = np.linspace(0, 2*np.pi,360) 
    xs = (radius*np.cos(theta) + x)
    ys = (radius*np.sin(theta) + y)
    if dynamic_elev:
        zs = get_elev(xs,ys)
        return xs, ys, zs
    else:
        return xs, ys

In [6]:
# calculate subplot1 location
def get_subplot1_loc(x,y):
    z = get_elev(x, y)
    plot_xs, plot_ys, plot_zs = get_plot_boundary(x, y, 58.9)
    return x, y, z, plot_xs, plot_ys, plot_zs

# generate graph objects for subplot1
def get_subplot1_gos(x,y):
    x, y, z, plot_xs, plot_ys, plot_zs = get_subplot1_loc(x,y)
    
    # make the graph objects
    subplot1_boundary = go.Scatter3d(x=plot_xs, y=plot_ys, z=plot_zs,
                                     marker={'size':0.1, 'opacity':1.0},
                                     line={'color':'black','width':5},
                                     hoverinfo='none',
                                     name='plot boundary'
                                    )
    subplot1_center = go.Scatter3d(x=[x], y=[y], z=[z], mode='markers',
                                   marker={'symbol':'circle', 'size':2, 'color':'black',
                                           'line':{'width':1}},
                                   opacity=0.9,
                                   name='plot center'
                                  )
    return subplot1_boundary, subplot1_center

In [7]:
# starting values and widgets
center_x, center_y = (r-l)/2 + l, (t-b)/2 + b

gps_x = widgets.IntSlider(value=center_x, min=l+58.9, max=r-58.9,step=1,
                          continuous_update=False, description='Plot Center Easting (X):',
                          layout=Layout(width='50%'),
                          style={'description_width': 'initial'})
gps_y = widgets.IntSlider(value=center_y, min=b+58.9, max=t-58.9, step=1,
                          continuous_update=False, description='Plot Center Northing (Y):',
                          layout=Layout(width='50%'),
                          style={'description_width': 'initial'})


subplot_layout = layout.copy()
subplot_layout.update(title = '<b>Move the coordinates of Subplot 1</b>')
    
# interactive plotting function
@interact(x=gps_x, y=gps_y, continuous_update=False)
def plot_subplot1(x,y):
    subplot1_boundary, subplot1_center = get_subplot1_gos(x,y)
    # create the figure
    fig = go.Figure(data=[static_terrain,subplot1_boundary,subplot1_center], layout=subplot_layout)
    iplot(fig)

interactive(children=(IntSlider(value=1324243, continuous_update=False, description='Plot Center Easting (X):'…

# 2. Record the location of a tree in subplot 1
Within each FIA subplot, the coordinates of each tree are calculated from the center of that subplot. The location of each tree, $j$, is recorded in the field using an azimuth ($az_{tree,obs}[j]$) and distance ($d_{tree,obs}[j]$) from the subplot center. 

We will convert from the field-recorded azimuth (bearing in degrees from North) to radians and re-orient to the Cartesian coordinate system: 

$\theta_{tree,obs} = \frac{(90- az_{tree}[j])}{2\pi}$

## Calculations
The (X,Y) coordinates of the stem locations in a subplot are made as:

$X_{tree}[j] = X_{plot}[i] + d_{tree}[j] \cdot cos(\theta_{tree}[j])$

$Y_{tree}[j] = Y_{plot}[i] + d_{tree}[j] \cdot sin(\theta_{tree}[j])$

The elevation of the tree stem at ground level will be calculated based on the elevation of a lidar-derived DEM at that (X,Y) location.

$Z_{tree}[j] = DEM[X_{tree}[j], Y_{tree}[j]]$


<img src='./images/step02.jpg' width='400' align='right'> 
## Interactions
Widgets allow user to adjust the bearing and distance of a tree from the center of the subplot.

In [8]:
def get_tree_loc(bearing, distance):
    # get the tree location
    theta_tree = np.deg2rad(90-bearing)
    x_tree = gps_x.value + distance*np.cos(theta_tree)
    y_tree = gps_y.value + distance*np.sin(theta_tree)
    # now get the elevation at this point
    z_tree = get_elev(x_tree,y_tree) # find out the index values for terrain raster
    
    return x_tree, y_tree, z_tree

def get_tree_go(bearing, distance):
    # generate a graph object for a tree stem location
    x_tree, y_tree, z_tree = get_tree_loc(bearing, distance)
    
    tree = go.Scatter3d(x=[x_tree], y=[y_tree], z=[z_tree], mode='markers',
                        marker={'symbol':'circle', 'size':10, 'color':'brown',
                                'line':{'width':1}},
                        opacity=0.9,
                        name='tree',
                        hoverinfo='none')
    return tree

def get_sightline_go(bearing,distance):
    # generate a graph object for the sight line to the tree stem
    x_tree, y_tree, z_tree = get_tree_loc(bearing, distance)
    sight_line = go.Scatter3d(x=[x_tree,gps_x.value], y=[y_tree,gps_y.value], 
                              z=[z_tree+5, get_elev(gps_x.value, gps_y.value)+5],
                              marker={'size':0.1, 'opacity':1.0},
                              line={'color':'orange','width':5},
                              hoverinfo='none',
                              name='sight line'
                             )
    return sight_line

In [9]:
bearing = widgets.IntSlider(value=270, min=0, max=360,step=1,
                            continuous_update=False, description='Bearing (deg):',
                            layout=Layout(width='50%'),
                            style={'description_width': 'initial'})
distance = widgets.FloatSlider(value=25, min=0, max=58.9, step=0.1,
                               continuous_update=False, description='Distance (ft):',
                               layout=Layout(width='50%'),
                               style={'description_width': 'initial'})

tree_layout = subplot_layout.copy()

# interactive plotting function
@interact(bearing=bearing, distance=distance, continuous_update=False)
def plot_tree(bearing, distance):
    # get the graph objects for the tree
    tree, sight_line = get_tree_go(bearing, distance), get_sightline_go(bearing,distance)
    # get the graph objects for the subplot
    subplot1_boundary, subplot1_center = get_subplot1_gos(gps_x.value,gps_y.value)
    
    scene = {
        'xaxis': {'title':'Easting', 'showgrid':False, 'showticklabels':False, 'zeroline':False, 'showspikes':False,
                 'range': [gps_x.value - 75, gps_x.value + 75]},
        'yaxis': {'title':'Northing', 'showgrid':False, 'showticklabels':False, 'zeroline':False, 'showspikes':False,
                 'range': [gps_y.value - 75, gps_y.value + 75]},
        'zaxis': {'title':'', 'showgrid':False, 'showticklabels':False, 'zeroline':False,  'showspikes':False},
        'camera':{'up':{'x':0, 'y':0, 'z':1},
          'center':{'x':0, 'y':0, 'z':0},
          'eye':{'x':-0.5, 'y':-2.0, 'z':0.65}}
        }
    tree_layout.update(title='<b>Change the location of the first tree on the subplot</b>', scene=scene)
    # render the figure
    fig = go.Figure(data=[static_terrain, subplot1_boundary, subplot1_center, tree, sight_line],layout=tree_layout)
    iplot(fig)

interactive(children=(IntSlider(value=270, continuous_update=False, description='Bearing (deg):', layout=Layou…

#### Prior Distributions
Both the bearing and the distance of a tree from subplot center are assumed to have normally-distributed measurement error: 

$\theta_{tree}[j] \sim N(\theta_{tree,obs}[j],\sigma_{compass})$

$d_{tree}[j] \sim N(d_{tree,obs}[j], \sigma_{dist})$ 

The re-use of $\sigma_{dist}$ assumes the error in measuring distance between plots is the same as the error in measuring distance to trees from a subplot center.

# 3. Record the height, and lean of the tree
The location of a tree top is calculated using the field-measured height, which may be offset in the X,Y directions from the location of the stem based on tree lean. The Z value of the tree top (height above ground) is * **not** * calculated above the DEM at the location of the * **tree top's** * X,Y coordinates. Rather, the Z value of a tree top (top height) is calculated based on observed tree height (with error) plus the elevation of the DEM at the X,Y location of the * **tree stem** *. Envision a right triangle with the height as the vertical side of triangle, and the hypotenuse is a particular angle (lean) from the vertical height measurement.

## Calculations
The X, Y, Z coordinates of each tree top can be calculated as:

$X_{treetop}[j] = X_{tree}[j] + \frac{1}{tan(\phi_{lean}[j])} \cdot height_{tree}[j] \cdot cos(\theta_{lean}[j])$

$Y_{treetop}[j] = Y_{tree}[j] + \frac{1}{tan(\phi_{lean}[j])} \cdot height_{tree}[j] \cdot sin(\theta_{lean}[j])$

$Z_{treetop}[j] = Z_{tree}[j] + height_{tree}[j]$

<img src='./images/step03.jpg' width='400' align='right'>
#### Interactions
Widgets allow the user to adjust the diameter, height, angle of lean, and direction of lean. The main stem will be visualized as a cone extending from it's location measured on the ground up to the location of the tree top.

In [10]:
def get_treetop_loc(height, lean_direction, lean_severity):
    # calculate the location of the tree top
    theta_lean = np.deg2rad(lean_direction) 
    # lean severity is measured in degrees from vertical, convert to degrees from horizontal
    phi_lean = np.deg2rad(90-lean_severity)
    
    # get tree stem location from current widget values
    x_tree, y_tree, z_tree = get_tree_loc(bearing.value, distance.value)
    
    # calculate location of tree top
    x_treetop = x_tree + 1/np.tan(phi_lean)*height*np.sin(theta_lean)
    y_treetop = y_tree + 1/np.tan(phi_lean)*height*np.cos(theta_lean)
    z_treetop = z_tree + height
    
    return x_treetop, y_treetop, z_treetop

def get_treetop_go(height, lean_direction, lean_severity):
    # generate a graph object for the tree stem
    # get tree stem location from current widget values
    x_tree, y_tree, z_tree = get_tree_loc(bearing.value, distance.value)
    
    # get tree top location
    x_treetop, y_treetop, z_treetop = get_treetop_loc(height, lean_direction, lean_severity)

    bole = go.Scatter3d(x=[x_tree, x_treetop], 
                        y=[y_tree, y_treetop], 
                        z=[z_tree, z_treetop], 
                        marker={'size':0.1, 'opacity':0.0},
                        line={'color':'brown','width':15},
                        hoverinfo='none',
                        name='bole')
    return bole

In [11]:
# create the widgets for controlling tree height and lean
# dbh = widgets.FloatSlider(value=5.8, min=0, max=35,step=0.1, 
#                             continuous_udpate=False, description='DBH (in):')
height = widgets.IntSlider(value=150, min=0, max=225,step=1, 
                           continuous_update=False, description='Height (ft):',
                           layout=Layout(width='50%'),
                           style={'description_width': 'initial'})
lean_direction = widgets.IntSlider(value=25, min=0, max=360, step=1,
                                   continuous_update=False, description='Lean Direction (deg):',
                                   layout=Layout(width='50%'),
                                   style={'description_width': 'initial'})
lean_severity = widgets.IntSlider(value=4, min=0, max=60, step=1,
                                  continuous_update=False, description='Lean Severity (deg):',
                                  layout=Layout(width='50%'),
                                  style={'description_width': 'initial'})

    
lean_layout = tree_layout.copy()


# generate the interactive plot
@interact(height=height, lean_direction=lean_direction, lean_severity=lean_severity, continuous_update=False)
def plot_treetop(height, lean_direction, lean_severity):
    tree = get_tree_go(bearing.value, distance.value)    
    subplot1_boundary, subplot1_center = get_subplot1_gos(gps_x.value,gps_y.value)
    bole = get_treetop_go(height, lean_direction, lean_severity)
    
    plot_z = get_elev(gps_x.value, gps_y.value)
    scene = {
    'xaxis': {'title': 'Eastings', 'showgrid': True, 'showticklabels':False, 'zeroline':False, 'showspikes':False,
              'range': [gps_x.value - 150, gps_x.value + 150]},
    'yaxis': {'title': 'Northings', 'showgrid': True, 'showticklabels':False, 'zeroline':False, 'showspikes':False,
              'range': [gps_y.value - 150, gps_y.value + 150]},
    'zaxis': {'title': 'Elevation', 'showgrid': True, 'showticklabels':False, 'zeroline':False, 'showspikes':False,
              'range': [plot_z - 10, plot_z + 290]},
        'camera':{'up':{'x':0, 'y':0, 'z':1},
          'center':{'x':0, 'y':0, 'z':0},
          'eye':{'x':0.1, 'y':-2.3, 'z':0.25}},
    'aspectratio':{'x':1, 'y':1, 'z':1}
        }
    lean_layout=tree_layout.copy()
    lean_layout.update(title='Change tree height, direction of lean, and severity of lean', scene=scene)
    
    fig = go.Figure(data=[static_terrain, subplot1_boundary, subplot1_center, tree, bole], layout=lean_layout)
    iplot(fig)

interactive(children=(IntSlider(value=150, continuous_update=False, description='Height (ft):', layout=Layout(…

#### Prior Distributions
Field-measured height ($height_{tree,obs}[j]$) will be modeled with normally-distributed measurement error. The direction of tree lean ($\phi_{lean}[j]$) is uniformly distributed across all possible bearings, i.e., equally as likely to point in any compass direction. The severity of lean ($\theta_{lean}[j]$), which reflects the divergence of the main tree stem from vertical, will be modeled using an exponential distribution (e.g., 90% of trees lean <10 degrees from vertical):

$height_{tree}[j] \sim N(height_{tree,obs}[j], \sigma_{height})$

$\phi_{lean}[j] \sim U[0,2\pi)$

$\theta_{lean}[j] \sim Exp(\lambda)$

# 4. Model a symmetric crown surface
A flexible geometric form, a generalized ellipsoid is used to approximate the three-dimensional crown surface of each tree. A two-dimensional ellipsoid for modeling crowns was originally proposed by Horn (1971): 

<img src='./images/Sheng et al 2001_Figure1.PNG' width='500' align='right'>
$\frac{x^E}{a^E}+\frac{y^E}{b^E}=1$

A three-dimensional variant has been attributed to Pollock (1996), and similar model was also described by Koop (1989).
This model is illustrated by Sheng et al. (2001), who referred to this as the Pollock model.


In [12]:
def get_crown(crown_ratio, crown_radius, curvature):
    cc = curvature
    top_ht = height.value
    
    # location of treetop
    xt, yt, zt = get_treetop_loc(height.value, lean_direction.value, lean_severity.value)
    x_tree, y_tree, z_tree = get_tree_loc(bearing.value, distance.value)
    
    cr = crown_radius * top_ht
    ch = top_ht * crown_ratio
    bh = top_ht - ch    
    
#    print('ZT {:.0f}, TOP {:.0f}, HT {}, CR {}, CL {:.0f}, CBH {:.0f}'.format(zt, z_tree + top_ht, top_ht, crown_ratio, ch, bh))
    
    # Set of all spherical angles:
    u = np.linspace(0, 2 * np.pi, 100)
    v = np.linspace(0, np.pi, 100)

    # Cartesian coordinates that correspond to the spherical angles:
    # (this is the equation of an ellipsoid):
    x = cr * np.outer(np.cos(u), np.sin(v)) + xt
    y = cr * np.outer(np.sin(u), np.sin(v)) + yt
    
    # generate surface points of the crown using Sheng et al. (2001) equation
    z = ((1-(((x-xt)**2 + (y-yt)**2)**(cc/2))/(cr**cc))*(ch**cc) - ch + zt)**(1/cc) + z_tree
#    print(z.max(), z.min(), z.max()-z.min())
    
    return x.flatten(), y.flatten(), z.flatten()

def get_crown_go(crown_ratio, crown_radius, curvature):
    # create graph object of crown
    xs, ys, zs = get_crown(crown_ratio, crown_radius, curvature)
    crown = go.Mesh3d(x=xs,y=ys,z=zs, color='green', opacity=0.3)
    return crown

<img src='./images/step04.jpg' width='400' align='right'>

## Interactions
Widgets allow user to adjust height to crown base, maximum crown radius, and crown curvature.

In [13]:
crown_ratio = widgets.FloatSlider(min=0.0,max=1.0,step=0.01,value=0.75,
                    description='Crown Ratio (% of Ht):',
                    continuous_update=False,
                    layout=Layout(width='50%'),
                    style={'description_width': 'initial'})
curvature = widgets.FloatSlider(min=0.01,max=5,step=0.01, value=1.5,
                        description='Curvature:',
                        continuous_update=False,
                        layout=Layout(width='50%'))
crown_radius = widgets.FloatSlider(min=0.01,max=1,step=.01,value=0.35,
                     description='Crown Radius (% of Ht):',
                     continuous_update=False,
                     layout=Layout(width='50%'),
                     style={'description_width': 'initial'})

# generate the interactive plot
@interact(crown_ratio=crown_ratio, crown_radius=crown_radius, curvature=curvature, continuous_update=False)
def plot_crown(crown_ratio, crown_radius, curvature):
    tree = get_tree_go(bearing.value, distance.value)    
    subplot1_boundary, subplot1_center = get_subplot1_gos(gps_x.value,gps_y.value)
    bole = get_treetop_go(height.value, lean_direction.value, lean_severity.value)
    crown = get_crown_go(crown_ratio, crown_radius, curvature)
    
    fig = go.Figure(data=[subplot1_boundary, subplot1_center, tree, bole, crown])
    iplot(fig)

interactive(children=(FloatSlider(value=0.75, continuous_update=False, description='Crown Ratio (% of Ht):', l…

# TODO

## 5. Incorporate asymmetry into the crown model

Cescatti (1997) elaborates on the model originally proposed by Horn (1971) and developed by Koop (1989), describing an asymmetric hull crown model in three dimensions, based on 4 crown radii measured in two orthogonal directions, the location of the tree top, and the location of the stem at the bottom of the live crown. This results in a set of eight profiles, four for the upper crown from each measured crown radius on the 'peripheral line' to the tree top, and four for the lower crown from each crown radius on the 'peripheral line' to the stem at the bottom of the live crown.

<img src='./images/Cescatti 1997_Figure1.PNG' width='400' align='left'><img src='./images/Cescatti 1997_Figure3.PNG' width='250' align='left'>

#### Interactions
Widgets allow user to adjust one of the crown profile lines, including maximum crown width, height to maximum crown width, and curvature above and below maximum crown width.




### Allowing neighborhood competition to influence crown asymmetry
Following Seidel et al. (2011), a modifier of crown symmetry may be incorporated based on the competitive influence of neighboring trees. A competition vector is formed for each tree, where the magnitude of the competition vector for each neighboring tree is its diameter at breast height divided by the square root of the distance between the two trees. The sum of these vectors represents the sum of all competitive pressure of the neighbors on the focal tree.

## 6. Add the remaining trees to subplot 1
<img src='./images/step06.jpg' width='400' align='right'>
Additional trees recorded on subplot 1 are automatically added to an interactive 3D visualization.

#### Interactions
No widgets to adjust tree and plot parameters. User can rotate, zoom.

## 7. Measure bearing and distance to center of subplot 2.
The centers of FIA subplots 2, 3, and 4 are calculated using a fixed bearing or azimuth, $\theta_{plot}[i]$, and a distance, $d_{plot}[i]$, of 120 ft from the center of subplot 1. Both the bearing/azimuth and the distance from the center of subplot 1 are assumed to have normally-distributed measurement error.

#### Calculations
<img src='./images/step07.jpg' width='400' align='right'>
For each additional subplot, $i$, where $i \in \{2, 3, 4\}$... the locations of subplots 2, 3, and 4 can be calculated as:

$X_{plot}[i] = X_{plot}[1] + d_{plot}[i]\cdot cos(\theta_{plot}[i])$

$Y_{plot}[i] = Y_{plot}[1] + d_{plot}[i]\cdot sin(\theta_{plot}[i])$

#### Interactions
Widgets enable interactive control of bearing and distance to subplot 2.

#### Prior Distributions

The distance of each plot from subplot 1, as well as the bearings of these subplots from subplot are modeled as: 

$d_{plot}[i] \sim N(120, \sigma_{dist})$

$\theta_{plot}[2] \sim N(\frac{\pi}{2}, \sigma_{compass})$

$\theta_{plot}[3] \sim N(\frac{11\pi}{6},\sigma_{compass})$

$\theta_{plot}[4] \sim N(\frac{7\pi}{6}, \sigma_{compass})$


## 8. Add trees to subplot 2
<img src='./images/step08.jpg' width='400' align='right'> 
The trees observed on subplot 2 are added to the 3D scene.
#### Interactions
No widgets. User can rotate and zoom the 3D visualization of subplots 1 and 2 with trees.

## 9. Add subplots 3 and 4, including trees.
<img src='./images/step09.jpg' width='400' align='right'>
The location of subplots 3 and 4, including trees observed in them will be visualized in 3D.

#### Interactions
No widgets. User can rotate and zoom 3D visualization of all subplots and trees.

## 10. Visualize all subplots and trees, with error.
<img src='./images/step10.jpg' width='400' align='right'>
Animated view of 3D scene, sampling through the probability distributions of the tree and subplot parameters.
